In [1]:
from lsst.daf.butler import Butler
import astropy

## Define embargo and scratch butler

In [8]:
butler = Butler('/repo/embargo')
registry = butler.registry

In [3]:
scratch_butler = Butler('/home/j/jarugula/scratch', writeable=True)
scratch_registry = scratch_butler.registry

In [4]:
#help(scratch_registry)

## Dataset to move

In [5]:
datasetType = 'raw'
collections = 'LATISS/raw/all'
#dataId = {'instrument': 'LATISS', 'detector': 0, 'band':'r'}
dataId = {'instrument': 'LATISS', 'band':'r'}
#dataId = {'instrument': 'LATISS'}

## Define embargo period 

In [9]:
embargo_period = astropy.time.TimeDelta(100, format='jd') # 30 julian days?
int_embargo_period = int(embargo_period.datetime.days)
now = astropy.time.Time.now()
int_now = int(now.datetime.strftime("%Y%m%d"))

print(embargo_period)
print(int_embargo_period)
print(now)
print(int_now)

100.0
100
2023-03-15 18:16:47.681360
20230315


## The Dimensions query 

with where statement ~ 3.02s and without takes about the same time.


If now - observation_end_time_in_embargo > embargo period :

    move
    
Else:

    Don't move
    
Save data Ids of these observations into a list

In [10]:
after_embargo = []
for i, dt in enumerate(registry.queryDimensionRecords('exposure',dataId=dataId,datasets=datasetType,collections=collections,
                                                     where="now - exposure.day_obs > embargo_period",
                                                     bind={"now": int_now, "embargo_period": int_embargo_period})):
    end_time = dt.timespan.end
    if now - end_time > embargo_period:
        after_embargo.append(dt.id)

In [11]:
len(after_embargo)

7299

## Query the DataIds after embargo period

In [12]:
datasetRefs = registry.queryDatasets(datasetType, dataId=dataId, collections=collections,
                                         where="exposure.id IN (exposure_ids)",
                                         bind={"exposure_ids": after_embargo})

In [13]:
for i, ref in enumerate(datasetRefs):
    print(ref.dataId.full)
    if i > 10:
        break

{band: 'r', instrument: 'LATISS', detector: 0, physical_filter: 'FELH0600~ronchi170lpmm', exposure: 2022091400696}
{band: 'r', instrument: 'LATISS', detector: 0, physical_filter: 'FELH0600~ronchi170lpmm', exposure: 2022091400708}
{band: 'r', instrument: 'LATISS', detector: 0, physical_filter: 'FELH0600~ronchi170lpmm', exposure: 2022091400714}
{band: 'r', instrument: 'LATISS', detector: 0, physical_filter: 'FELH0600~ronchi170lpmm', exposure: 2022091400734}
{band: 'r', instrument: 'LATISS', detector: 0, physical_filter: 'FELH0600~ronchi170lpmm', exposure: 2022091400728}
{band: 'r', instrument: 'LATISS', detector: 0, physical_filter: 'FELH0600~ronchi170lpmm', exposure: 2022091400746}
{band: 'r', instrument: 'LATISS', detector: 0, physical_filter: 'FELH0600~ronchi170lpmm', exposure: 2022091400752}
{band: 'r', instrument: 'LATISS', detector: 0, physical_filter: 'FELH0600~ronchi170lpmm', exposure: 2022092800729}
{band: 'r', instrument: 'LATISS', detector: 0, physical_filter: 'FELH0600~ronchi

## Copy the Dataset after embargo period from embargo butler to scratch butler

In [14]:
scratch_butler.transfer_from(butler, source_refs=datasetRefs, transfer='copy',skip_missing=True,register_dataset_types=True,transfer_dimensions=True)

[DatasetRef(DatasetType('raw', {band, instrument, detector, physical_filter, exposure}, Exposure), {instrument: 'LATISS', detector: 0, exposure: 2022092900969, ...}, id=0021f153-0fac-5a4e-ba91-1de530d65700, run='LATISS/raw/all'),
 DatasetRef(DatasetType('raw', {band, instrument, detector, physical_filter, exposure}, Exposure), {instrument: 'LATISS', detector: 0, exposure: 2022102500714, ...}, id=007102b4-a5d8-5dbb-9038-f9ef2ebd6b2e, run='LATISS/raw/all'),
 DatasetRef(DatasetType('raw', {band, instrument, detector, physical_filter, exposure}, Exposure), {instrument: 'LATISS', detector: 0, exposure: 2022100500149, ...}, id=00786f81-0b54-5e96-8b5a-01cbd08a80f6, run='LATISS/raw/all'),
 DatasetRef(DatasetType('raw', {band, instrument, detector, physical_filter, exposure}, Exposure), {instrument: 'LATISS', detector: 0, exposure: 2022101200984, ...}, id=007b180a-6fc8-5396-a02c-e4226fc214e2, run='LATISS/raw/all'),
 DatasetRef(DatasetType('raw', {band, instrument, detector, physical_filter, exp

## Check if the copied data exists in scratch butler

In [7]:
transferred_datasetRefs_all = scratch_registry.queryDatasets(datasetType, dataId=dataId, collections=collections)
for i, ref in enumerate(transferred_datasetRefs_all):
    print(ref.dataId.full)
    if i > 10:
        break
     

MissingCollectionError: No collection with name 'LATISS/raw/all' found.

In [13]:
len(list(transferred_datasetRefs_all))

7268

In [14]:
# # Using loop instead of IN
# for i,exposure_id in enumerate(after_embargo[0:10]):
#     datasetRefs = registry.queryDatasets(datasetType, dataId=dataId, collections=collections,
#                                          where="exposure.id = exposure_id",
#                                          bind={"exposure_id": exposure_id})
#     scratch_butler.transfer_from(butler, source_refs=datasetRefs, transfer='copy',skip_missing=True,register_dataset_types=True,transfer_dimensions=True)
    

In [15]:
# transferred_datasetRefs = scratch_registry.queryDatasets(datasetType, dataId=dataId, collections=collections,
#                                     where="exposure.id = exposure_id",
#                                     # bind={"exposure_id": 2022110300001}
#                                     bind={"exposure_id": 2022101201223})
# for i, ref in enumerate(transferred_datasetRefs):
#     print(ref.dataId.full)

## Remove data

In [6]:
#scratch_registry.removeCollection(collections) 
scratch_butler.pruneCollection(collections, purge=True, unstore=True)